## The following are standard UNIX shell commands run inside of a Notebook Cell

In [ ]:
!ls -l data/

In [ ]:
!head data/VibrioCholerae.fa

In [ ]:
!tail -5 data/VibrioCholerae.fa

In [ ]:
!wc data/*.fa

## Next we write and execute Python3 inside of a Notebook Cell

In [ ]:
import gzip

def loadFasta(filename):
    """ Parses a classically formatted and possibly 
        compressed FASTA file into two lists. One of 
        headers and a second list of sequences.
        The ith index of each list correspond."""
    if (filename.endswith(".gz")):
        fp = gzip.open(filename, 'r')
    else:
        fp = open(filename, 'r')
    # split at headers
    data = fp.read().split('>')
    fp.close()
    # ignore whatever appears before the 1st header
    data.pop(0)     
    headers = []
    sequences = []
    for sequence in data:
        lines = sequence.split('\n')
        headers.append(lines.pop(0))
        # add an extra "+" to make string "1-referenced"
        sequences.append('+' + ''.join(lines))
    return (headers, sequences)

In [ ]:
header, seq = loadFasta("data/VibrioCholerae.fa")

for i in range(len(header)):
    print(header[i])
    print(len(seq[i])-1, "bases", seq[i][:30], "...", seq[i][-30:])
    print()

## Use *k*-mer profiles to study a DNA sequence

In [ ]:
def kmerCounts(seq, k):
    kmerDict = {}
    for i in range(1,len(seq)-k+1):
        kmer = seq[i:i+k]
        kmerDict[kmer] = kmerDict.get(kmer,0) + 1
    return kmerDict

In [ ]:
# Test code for the kmerCounts() function
print(kmerCounts("+TAGACAT",3))
print(kmerCounts("+missmississippi",3))

In [ ]:
print('  k     k-mers              4^k      N-k+1          missing   repeated')
for k in range(3,25):
    kmers = kmerCounts(seq[0], k)
    print("%3d %10d %16d %10d %16d %10d" % (k, len(kmers), 4**k, (len(seq[0])-1)-k+1, 4**k-len(kmers), (len(seq[0])-1)-k+1-len(kmers)))

## Back to Biology...
Next we extract a known oriC region to look for patterns.

In [ ]:
genome = seq[0]
print("oriC:")
OriCStart = 151887
oriC = genome[OriCStart:OriCStart+540]
for i in range(9):
    print("    %s" % oriC[60*i:60*(i+1)].lower())

In [ ]:
def mostFreqKmer(start, end, sequence):
    for k in range(start,end):
        kmerStats = kmerCounts(sequence,k)
        kmerOrder = sorted(kmerStats, reverse=True, key=kmerStats.get)
        mostFreq = [(kmer, kmerStats[kmer]) for kmer in kmerOrder[0:6]]
        print(k, mostFreq)

mostFreqKmer(1,10,oriC)